# Solving CartPole using Q Learning Tabular Method

In [1]:
import gym 
import numpy as np 
import math 
import random

In [2]:
env = gym.make('CartPole-v0')

In [3]:
result = []
observ = env.reset()
for t in range(300):
    env.render()
    action = env.action_space.sample()
    observ, reward, done, info = env.step(action)
    result.append([action, reward])

C:\Users\Nagabhushanam\Anaconda3\lib\site-packages\gym\logger.py:30: UserWarning: WARN: You are calling 'step()' even though this environment has already returned done = True. You should always call 'reset()' once you receive 'done = True' -- any further steps are undefined behavior.
  warnings.warn(colorize('%s: %s'%('WARN', msg % args), 'yellow'))


In [4]:
env.close()

In [5]:
#actions are move cart left or right 
print(env.action_space)

Discrete(2)


In [6]:
# observation space: has four values 
'''
position of cart
velocity of cart
angle of pole
angular velocity of pole 
'''
print(env.observation_space)

Box(-3.4028234663852886e+38, 3.4028234663852886e+38, (4,), float32)


In [7]:
print(env.observation_space.low)

[-4.8000002e+00 -3.4028235e+38 -4.1887903e-01 -3.4028235e+38]


In [8]:
print(env.observation_space.high)

[4.8000002e+00 3.4028235e+38 4.1887903e-01 3.4028235e+38]


######  Discretize the state space so we can apply Q learning to a bounded space

In [9]:
num_buckets = [1,1,6,3]
num_actions = env.action_space.n
state_bounds = list(zip(env.observation_space.low, env.observation_space.high))

In [10]:
# amend the state bound ranges for velocity and pole angle 
state_bounds[1] = [-0.5, 0.5]
state_bounds[3] = [-math.radians(50),math.radians(50)]
state_bounds

[(-4.8, 4.8),
 [-0.5, 0.5],
 (-0.41887903, 0.41887903),
 [-0.8726646259971648, 0.8726646259971648]]

In [11]:
q_table = np.zeros(num_buckets +[num_actions])
print(q_table.shape)
q_table

(1, 1, 6, 3, 2)


array([[[[[0., 0.],
          [0., 0.],
          [0., 0.]],

         [[0., 0.],
          [0., 0.],
          [0., 0.]],

         [[0., 0.],
          [0., 0.],
          [0., 0.]],

         [[0., 0.],
          [0., 0.],
          [0., 0.]],

         [[0., 0.],
          [0., 0.],
          [0., 0.]],

         [[0., 0.],
          [0., 0.],
          [0., 0.]]]]])

In [12]:
explore_rate_min = 0.01
learning_rate_min = 0.1

In [13]:
def get_explore_rate(t):
    return max(explore_rate_min, min(1, 1.0-math.log10((t+1)/25)))

In [14]:
def get_learning_rate(t):
    return max(learning_rate_min,min(1, 1.0-math.log10((t+1)/25)))

In [15]:
def select_action(state, explore_rate):
    if random.random() < explore_rate:
        action = env.action_space.sample()
    else: 
        action = np.argmax(q_table[state])
    return action

In [16]:
def state_to_bucket(state):
    bucket_indices =[]
    for i in range(len(state)):
        if state[i]<=state_bounds[i][0]:
            bucket_index = 0
        elif  state[i]>=state_bounds[i][1]:
            bucket_index = num_buckets[i]-1
        else:
            bound_width = state_bounds[i][1]-state_bounds[i][0]
            offset = (num_buckets[i]-1)* state_bounds[i][0]/bound_width
            scaling = (num_buckets[i]-1)/bound_width
            bucket_index = int(round(scaling*state[i]-offset))

        bucket_indices.append(bucket_index)

    return tuple(bucket_indices)

In [17]:
def simulate():
    learning_rate = get_learning_rate(0)
    explore_rate = get_explore_rate(0)
    
    discount_factor = 0.99
    num_streaks = 0
    
    for episode in range(1000):
        observ = env.reset()
        state_0 = state_to_bucket(observ)
        for t in range(300):
            env.render()
            action = select_action(state_0, explore_rate)
            observ, reward, done, info = env.step(action)
            state = state_to_bucket(observ)
            best_q = np.amax(q_table[state])
            
            q_table[state_0 + (action,)] += \
            learning_rate* (reward + discount_factor*(best_q) - q_table[state_0+ (action, ) ])
            
            state_0 = state
            
            print("\nEpisode = %d" % episode)
            print('t=%d' %t)
            print('Action: %d' %action)
            print('State:', state)
            print('Reward:', reward)
            print('Best Q:', best_q)
            print('Explore rate:', explore_rate)
            print('Learning rate:', learning_rate)
            print('Streaks:', num_streaks)
            
            print('')
            
            if done: 
                print("Episode %d finished after %f time steps" %(episode, t))
                
                if (t>=199):
                    num_streaks +=1
                else:
                    num_streaks = 0
                break
        if num_streaks >120:
            break
        explore_rate = get_explore_rate(episode)
        learning_rate = get_learning_rate(episode)


In [18]:
simulate()


Episode = 0
t=0
Action: 1
State: (0, 0, 3, 1)
Reward: 1.0
Best Q: 0.0
Explore rate: 1
Learning rate: 1
Streaks: 0


Episode = 0
t=1
Action: 0
State: (0, 0, 3, 1)
Reward: 1.0
Best Q: 1.0
Explore rate: 1
Learning rate: 1
Streaks: 0


Episode = 0
t=2
Action: 0
State: (0, 0, 3, 1)
Reward: 1.0
Best Q: 1.99
Explore rate: 1
Learning rate: 1
Streaks: 0


Episode = 0
t=3
Action: 1
State: (0, 0, 3, 1)
Reward: 1.0
Best Q: 2.9701
Explore rate: 1
Learning rate: 1
Streaks: 0


Episode = 0
t=4
Action: 1
State: (0, 0, 3, 1)
Reward: 1.0
Best Q: 3.9403989999999998
Explore rate: 1
Learning rate: 1
Streaks: 0


Episode = 0
t=5
Action: 1
State: (0, 0, 3, 0)
Reward: 1.0
Best Q: 0.0
Explore rate: 1
Learning rate: 1
Streaks: 0


Episode = 0
t=6
Action: 0
State: (0, 0, 3, 1)
Reward: 1.0
Best Q: 2.9701
Explore rate: 1
Learning rate: 1
Streaks: 0


Episode = 0
t=7
Action: 0
State: (0, 0, 3, 1)
Reward: 1.0
Best Q: 2.9701
Explore rate: 1
Learning rate: 1
Streaks: 0


Episode = 0
t=8
Action: 0
State: (0, 0, 3, 1)



Episode = 2
t=23
Action: 0
State: (0, 0, 2, 1)
Reward: 1.0
Best Q: 10.466174574128358
Explore rate: 1
Learning rate: 1
Streaks: 0


Episode = 2
t=24
Action: 1
State: (0, 0, 2, 0)
Reward: 1.0
Best Q: 11.361512828387074
Explore rate: 1
Learning rate: 1
Streaks: 0


Episode = 2
t=25
Action: 0
State: (0, 0, 2, 1)
Reward: 1.0
Best Q: 12.247897700103204
Explore rate: 1
Learning rate: 1
Streaks: 0


Episode = 2
t=26
Action: 1
State: (0, 0, 2, 0)
Reward: 1.0
Best Q: 13.125418723102172
Explore rate: 1
Learning rate: 1
Streaks: 0


Episode = 2
t=27
Action: 1
State: (0, 0, 2, 0)
Reward: 1.0
Best Q: 13.125418723102172
Explore rate: 1
Learning rate: 1
Streaks: 0


Episode = 2
t=28
Action: 0
State: (0, 0, 2, 0)
Reward: 1.0
Best Q: 13.99416453587115
Explore rate: 1
Learning rate: 1
Streaks: 0


Episode = 2
t=29
Action: 1
State: (0, 0, 2, 0)
Reward: 1.0
Best Q: 14.854222890512439
Explore rate: 1
Learning rate: 1
Streaks: 0


Episode = 2
t=30
Action: 1
State: (0, 0, 2, 0)
Reward: 1.0
Best Q: 15.705680


Episode = 5
t=6
Action: 0
State: (0, 0, 2, 1)
Reward: 1.0
Best Q: 28.22694674017248
Explore rate: 1
Learning rate: 1
Streaks: 0


Episode = 5
t=7
Action: 0
State: (0, 0, 2, 2)
Reward: 1.0
Best Q: 15.705680661607312
Explore rate: 1
Learning rate: 1
Streaks: 0


Episode = 5
t=8
Action: 1
State: (0, 0, 2, 1)
Reward: 1.0
Best Q: 28.22694674017248
Explore rate: 1
Learning rate: 1
Streaks: 0


Episode = 5
t=9
Action: 0
State: (0, 0, 2, 2)
Reward: 1.0
Best Q: 28.944677272770754
Explore rate: 1
Learning rate: 1
Streaks: 0


Episode = 5
t=10
Action: 0
State: (0, 0, 3, 2)
Reward: 1.0
Best Q: 16.54862385499124
Explore rate: 1
Learning rate: 1
Streaks: 0


Episode = 5
t=11
Action: 0
State: (0, 0, 3, 2)
Reward: 1.0
Best Q: 16.54862385499124
Explore rate: 1
Learning rate: 1
Streaks: 0


Episode = 5
t=12
Action: 1
State: (0, 0, 3, 2)
Reward: 1.0
Best Q: 17.383137616441328
Explore rate: 1
Learning rate: 1
Streaks: 0


Episode = 5
t=13
Action: 1
State: (0, 0, 3, 2)
Reward: 1.0
Best Q: 18.2093062402769

State: (0, 0, 3, 1)
Reward: 1.0
Best Q: 27.501966404214627
Explore rate: 1
Learning rate: 1
Streaks: 0


Episode = 9
t=1
Action: 1
State: (0, 0, 3, 0)
Reward: 1.0
Best Q: 22.995685419484467
Explore rate: 1
Learning rate: 1
Streaks: 0


Episode = 9
t=2
Action: 0
State: (0, 0, 3, 1)
Reward: 1.0
Best Q: 27.501966404214627
Explore rate: 1
Learning rate: 1
Streaks: 0


Episode = 9
t=3
Action: 0
State: (0, 0, 3, 1)
Reward: 1.0
Best Q: 27.501966404214627
Explore rate: 1
Learning rate: 1
Streaks: 0


Episode = 9
t=4
Action: 1
State: (0, 0, 3, 1)
Reward: 1.0
Best Q: 28.22694674017248
Explore rate: 1
Learning rate: 1
Streaks: 0


Episode = 9
t=5
Action: 0
State: (0, 0, 3, 1)
Reward: 1.0
Best Q: 28.944677272770754
Explore rate: 1
Learning rate: 1
Streaks: 0


Episode = 9
t=6
Action: 1
State: (0, 0, 3, 1)
Reward: 1.0
Best Q: 29.655230500043047
Explore rate: 1
Learning rate: 1
Streaks: 0


Episode = 9
t=7
Action: 0
State: (0, 0, 3, 1)
Reward: 1.0
Best Q: 30.358678195042614
Explore rate: 1
Learning 


Episode = 10
t=30
Action: 0
State: (0, 0, 2, 1)
Reward: 1.0
Best Q: 41.29632180625153
Explore rate: 1
Learning rate: 1
Streaks: 0


Episode = 10
t=31
Action: 0
State: (0, 0, 2, 1)
Reward: 1.0
Best Q: 41.29632180625153
Explore rate: 1
Learning rate: 1
Streaks: 0


Episode = 10
t=32
Action: 0
State: (0, 0, 2, 1)
Reward: 1.0
Best Q: 41.88335858818901
Explore rate: 1
Learning rate: 1
Streaks: 0


Episode = 10
t=33
Action: 1
State: (0, 0, 2, 1)
Reward: 1.0
Best Q: 42.46452500230712
Explore rate: 1
Learning rate: 1
Streaks: 0


Episode = 10
t=34
Action: 0
State: (0, 0, 2, 1)
Reward: 1.0
Best Q: 43.03987975228405
Explore rate: 1
Learning rate: 1
Streaks: 0


Episode = 10
t=35
Action: 1
State: (0, 0, 2, 1)
Reward: 1.0
Best Q: 43.60948095476121
Explore rate: 1
Learning rate: 1
Streaks: 0


Episode = 10
t=36
Action: 0
State: (0, 0, 2, 1)
Reward: 1.0
Best Q: 44.1733861452136
Explore rate: 1
Learning rate: 1
Streaks: 0


Episode = 10
t=37
Action: 1
State: (0, 0, 2, 1)
Reward: 1.0
Best Q: 44.73165

...


Episode = 293
t=92
Action: 0
State: (0, 0, 2, 1)
Reward: 1.0
Best Q: 99.8684445167969
Explore rate: 0.01
Learning rate: 0.1
Streaks: 119


Episode = 293
t=93
Action: 0
State: (0, 0, 2, 2)
Reward: 1.0
Best Q: 99.86846379828017
Explore rate: 0.01
Learning rate: 0.1
Streaks: 119


Episode = 293
t=94
Action: 1
State: (0, 0, 3, 1)
Reward: 1.0
Best Q: 99.86904500945305
Explore rate: 0.01
Learning rate: 0.1
Streaks: 119


Episode = 293
t=95
Action: 1
State: (0, 0, 3, 1)
Reward: 1.0
Best Q: 99.86904500945305
Explore rate: 0.01
Learning rate: 0.1
Streaks: 119


Episode = 293
t=96
Action: 1
State: (0, 0, 3, 1)
Reward: 1.0
Best Q: 99.8691759644436
Explore rate: 0.01
Learning rate: 0.1
Streaks: 119


Episode = 293
t=97
Action: 1
State: (0, 0, 3, 0)
Reward: 1.0
Best Q: 99.86817972051387
Explore rate: 0.01
Learning rate: 0.1
Streaks: 119


Episode = 293
t=98
Action: 0
State: (0, 0, 2, 1)
Reward: 1.0
Best Q: 99.86869638108183
Explore rate: 0.01
Learning rate: 0.1
Streaks: 119


Episode = 293
t=99
Ac

Learning rate: 0.1
Streaks: 119


Episode = 293
t=152
Action: 1
State: (0, 0, 3, 1)
Reward: 1.0
Best Q: 99.87043140858195
Explore rate: 0.01
Learning rate: 0.1
Streaks: 119


Episode = 293
t=153
Action: 1
State: (0, 0, 3, 0)
Reward: 1.0
Best Q: 99.86947311909219
Explore rate: 0.01
Learning rate: 0.1
Streaks: 119


Episode = 293
t=154
Action: 0
State: (0, 0, 2, 1)
Reward: 1.0
Best Q: 99.86987062676513
Explore rate: 0.01
Learning rate: 0.1
Streaks: 119


Episode = 293
t=155
Action: 0
State: (0, 0, 2, 1)
Reward: 1.0
Best Q: 99.86987062676513
Explore rate: 0.01
Learning rate: 0.1
Streaks: 119


Episode = 293
t=156
Action: 0
State: (0, 0, 2, 1)
Reward: 1.0
Best Q: 99.87000075613837
Explore rate: 0.01
Learning rate: 0.1
Streaks: 119


Episode = 293
t=157
Action: 0
State: (0, 0, 2, 2)
Reward: 1.0
Best Q: 99.8699958805599
Explore rate: 0.01
Learning rate: 0.1
Streaks: 119


Episode = 293
t=158
Action: 1
State: (0, 0, 3, 1)
Reward: 1.0
Best Q: 99.87058271824615
Explore rate: 0.01
Learning rate:


Episode = 294
t=10
Action: 0
State: (0, 0, 2, 1)
Reward: 1.0
Best Q: 99.87159208865482
Explore rate: 0.01
Learning rate: 0.1
Streaks: 120


Episode = 294
t=11
Action: 0
State: (0, 0, 2, 1)
Reward: 1.0
Best Q: 99.87159208865482
Explore rate: 0.01
Learning rate: 0.1
Streaks: 120


Episode = 294
t=12
Action: 0
State: (0, 0, 2, 1)
Reward: 1.0
Best Q: 99.87172049656617
Explore rate: 0.01
Learning rate: 0.1
Streaks: 120


Episode = 294
t=13
Action: 0
State: (0, 0, 2, 2)
Reward: 1.0
Best Q: 99.87129328880054
Explore rate: 0.01
Learning rate: 0.1
Streaks: 120


Episode = 294
t=14
Action: 1
State: (0, 0, 3, 1)
Reward: 1.0
Best Q: 99.87168639152398
Explore rate: 0.01
Learning rate: 0.1
Streaks: 120


Episode = 294
t=15
Action: 1
State: (0, 0, 3, 1)
Reward: 1.0
Best Q: 99.87168639152398
Explore rate: 0.01
Learning rate: 0.1
Streaks: 120


Episode = 294
t=16
Action: 1
State: (0, 0, 3, 1)
Reward: 1.0
Best Q: 99.87181470513245
Explore rate: 0.01
Learning rate: 0.1
Streaks: 120


Episode = 294
t=17



Episode = 294
t=77
Action: 1
State: (0, 0, 3, 1)
Reward: 1.0
Best Q: 99.87258747290055
Explore rate: 0.01
Learning rate: 0.1
Streaks: 120


Episode = 294
t=78
Action: 1
State: (0, 0, 3, 1)
Reward: 1.0
Best Q: 99.87271488542765
Explore rate: 0.01
Learning rate: 0.1
Streaks: 120


Episode = 294
t=79
Action: 1
State: (0, 0, 3, 0)
Reward: 1.0
Best Q: 99.87212151150153
Explore rate: 0.01
Learning rate: 0.1
Streaks: 120


Episode = 294
t=80
Action: 0
State: (0, 0, 2, 1)
Reward: 1.0
Best Q: 99.87271879627387
Explore rate: 0.01
Learning rate: 0.1
Streaks: 120


Episode = 294
t=81
Action: 0
State: (0, 0, 2, 1)
Reward: 1.0
Best Q: 99.87271879627387
Explore rate: 0.01
Learning rate: 0.1
Streaks: 120


Episode = 294
t=82
Action: 0
State: (0, 0, 2, 1)
Reward: 1.0
Best Q: 99.8728460774776
Explore rate: 0.01
Learning rate: 0.1
Streaks: 120


Episode = 294
t=83
Action: 0
State: (0, 0, 2, 2)
Reward: 1.0
Best Q: 99.87245668260769
Explore rate: 0.01
Learning rate: 0.1
Streaks: 120


Episode = 294
t=84
A

Explore rate: 0.01
Learning rate: 0.1
Streaks: 120


Episode = 294
t=136
Action: 1
State: (0, 0, 3, 1)
Reward: 1.0
Best Q: 99.87387749073183
Explore rate: 0.01
Learning rate: 0.1
Streaks: 120


Episode = 294
t=137
Action: 1
State: (0, 0, 3, 1)
Reward: 1.0
Best Q: 99.87387749073183
Explore rate: 0.01
Learning rate: 0.1
Streaks: 120


Episode = 294
t=138
Action: 1
State: (0, 0, 3, 1)
Reward: 1.0
Best Q: 99.8740036132411
Explore rate: 0.01
Learning rate: 0.1
Streaks: 120


Episode = 294
t=139
Action: 1
State: (0, 0, 3, 0)
Reward: 1.0
Best Q: 99.87313735754779
Explore rate: 0.01
Learning rate: 0.1
Streaks: 120


Episode = 294
t=140
Action: 0
State: (0, 0, 2, 1)
Reward: 1.0
Best Q: 99.87451600914031
Explore rate: 0.01
Learning rate: 0.1
Streaks: 120


Episode = 294
t=141
Action: 0
State: (0, 0, 2, 1)
Reward: 1.0
Best Q: 99.87451600914031
Explore rate: 0.01
Learning rate: 0.1
Streaks: 120


Episode = 294
t=142
Action: 0
State: (0, 0, 2, 1)
Reward: 1.0
Best Q: 99.87464149313116
Explore rate: 

In [19]:
env.close()

######  State action table 

In [20]:
q_table

array([[[[[ 0.        ,  0.        ],
          [ 0.        ,  0.        ],
          [ 0.        ,  0.        ]],

         [[72.32116405, 73.9784133 ],
          [52.18025505, 73.9363331 ],
          [40.42120602, 33.20650437]],

         [[99.87191113, 98.6750309 ],
          [99.87573952, 99.70213473],
          [98.89585788, 99.87545661]],

         [[99.87415673, 99.32989218],
          [99.5272281 , 99.87504384],
          [98.09661538, 99.86919502]],

         [[ 3.940399  ,  0.        ],
          [54.12191014, 51.23599749],
          [51.98114376, 54.41309887]],

         [[ 0.        ,  0.        ],
          [ 0.        ,  0.        ],
          [ 0.        ,  0.        ]]]]])